In [2]:
import gym
import random
import csv
import time
from itertools import product
from stable_baselines3 import PPO
from stable_baselines3.common.evaluation import evaluate_policy


# NEED TO EDIT THESE
learning_rates = [0.1, 0.01, 0.001]
n_steps = [512]
batch_sizes = [128]
gammas = [0.9, 0.95, 0.99]
gae_lambdas = [0.95, 0.90]
clip_ranges = [0.1, 0.3, 0.5]
ent_coefs = [0.1, 0.01, 0.001]
epsilons = [1e-5]

#3x2x3x3x5x3x2 = 1620 times by 12.5 minutes = 20250 minutes
#need to reduce
#3x2x3x3x3x3x2 = 972 times by 12.5 = 12150 mins?
#need to reduce
#162 now times 12.5 is 2025 minutes so lets do 500,000 episodes a go at these parameters


# Define the best hyperparameters and best score seen so far
best_hyperparams = None
best_score = -float('inf')

with open('hyperparam_results_grid_search_mujoco_500thousand.csv', 'a', newline='') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(['learning_rate', 'n_steps', 'batch_size', 'gamma', 'gae_lambda', 'clip_range', 'ent_coef', 'epsilon', 'mean_reward', 'training_time', 'standard deviation'])

    for hyperparams in product(learning_rates, n_steps, batch_sizes, gammas, gae_lambdas, clip_ranges, ent_coefs, epsilons):
        learning_rate, n_steps, batch_size, gamma, gae_lambda, clip_range, ent_coef, epsilon = hyperparams

        env = gym.make('InvertedDoublePendulum-v2')

        model = PPO('MlpPolicy', env,
                    learning_rate=learning_rate,
                    n_steps=n_steps,
                    batch_size=batch_size,
                    gamma=gamma,
                    gae_lambda=gae_lambda,
                    clip_range=clip_range,
                    ent_coef=ent_coef,
                    clip_range_vf=epsilon,
                    verbose=1)

        print("Training with hyperparameters:", hyperparams)

        start_time = time.time()
        model.learn(total_timesteps=500000)
        end_time = time.time()

        training_time = end_time - start_time

        mean_reward, std_reward = evaluate_policy(model, env, n_eval_episodes=10)
        print("Mean reward: {:.2f} +/- {:.2f}".format(mean_reward, std_reward))

        if mean_reward > best_score:
            best_hyperparams = hyperparams
            best_score = mean_reward
            print("New best hyperparameters found:", best_hyperparams)
            print("New best score found:", best_score)

        with open('hyperparam_results_grid_search_mujoco_500thousand.csv', 'a', newline='') as csvfile:
            writer = csv.writer(csvfile)
            writer.writerow((learning_rate, n_steps, batch_size, gamma, gae_lambda, clip_range, ent_coef, epsilon, mean_reward,training_time, std_reward))

    print("Best hyperparameters:", best_hyperparams)
    print("Best score:", best_score)


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Training with hyperparameters: (0.1, 512, 128, 0.9, 0.95, 0.1, 0.1, 1e-05)
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 5.45     |
|    ep_rew_mean     | 49.3     |
| time/              |          |
|    fps             | 2032     |
|    iterations      | 1        |
|    time_elapsed    | 0        |
|    total_timesteps | 512      |
---------------------------------
---------------------------------------
| rollout/                |           |
|    ep_len_mean          | 4.43      |
|    ep_rew_mean          | 39.8      |
| time/                   |           |
|    fps                  | 1639      |
|    iterations           | 2         |
|    time_elapsed         | 0         |
|    total_timesteps      | 1024      |
| train/                  |           |
|    approx_kl            | 1.5818456 |
|    clip_fraction        | 0.972     |
|    clip_r

-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 5.4         |
|    ep_rew_mean          | 48.7        |
| time/                   |             |
|    fps                  | 1499        |
|    iterations           | 10          |
|    time_elapsed         | 3           |
|    total_timesteps      | 5120        |
| train/                  |             |
|    approx_kl            | 0.009775231 |
|    clip_fraction        | 0.251       |
|    clip_range           | 0.1         |
|    clip_range_vf        | 1e-05       |
|    entropy_loss         | -4.72       |
|    explained_variance   | -0.098      |
|    learning_rate        | 0.1         |
|    loss                 | 215         |
|    n_updates            | 90          |
|    policy_gradient_loss | -0.00502    |
|    std                  | 28.2        |
|    value_loss           | 469         |
-----------------------------------------
----------------------------------

-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 6.78        |
|    ep_rew_mean          | 61.5        |
| time/                   |             |
|    fps                  | 1498        |
|    iterations           | 19          |
|    time_elapsed         | 6           |
|    total_timesteps      | 9728        |
| train/                  |             |
|    approx_kl            | 0.009036813 |
|    clip_fraction        | 0.245       |
|    clip_range           | 0.1         |
|    clip_range_vf        | 1e-05       |
|    entropy_loss         | -4.91       |
|    explained_variance   | 0.0601      |
|    learning_rate        | 0.1         |
|    loss                 | 141         |
|    n_updates            | 180         |
|    policy_gradient_loss | -0.00912    |
|    std                  | 33.8        |
|    value_loss           | 306         |
-----------------------------------------
----------------------------------

-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 7.67        |
|    ep_rew_mean          | 69.9        |
| time/                   |             |
|    fps                  | 1490        |
|    iterations           | 28          |
|    time_elapsed         | 9           |
|    total_timesteps      | 14336       |
| train/                  |             |
|    approx_kl            | 0.029024445 |
|    clip_fraction        | 0.279       |
|    clip_range           | 0.1         |
|    clip_range_vf        | 1e-05       |
|    entropy_loss         | -4.99       |
|    explained_variance   | 0.134       |
|    learning_rate        | 0.1         |
|    loss                 | 216         |
|    n_updates            | 270         |
|    policy_gradient_loss | -0.00113    |
|    std                  | 34.7        |
|    value_loss           | 394         |
-----------------------------------------
----------------------------------

-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 7.97        |
|    ep_rew_mean          | 72.7        |
| time/                   |             |
|    fps                  | 1492        |
|    iterations           | 37          |
|    time_elapsed         | 12          |
|    total_timesteps      | 18944       |
| train/                  |             |
|    approx_kl            | 0.016908424 |
|    clip_fraction        | 0.146       |
|    clip_range           | 0.1         |
|    clip_range_vf        | 1e-05       |
|    entropy_loss         | -5          |
|    explained_variance   | -0.414      |
|    learning_rate        | 0.1         |
|    loss                 | 232         |
|    n_updates            | 360         |
|    policy_gradient_loss | -0.000661   |
|    std                  | 34.6        |
|    value_loss           | 440         |
-----------------------------------------
----------------------------------

...

------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 5.05         |
|    ep_rew_mean          | 45.4         |
| time/                   |              |
|    fps                  | 1202         |
|    iterations           | 305          |
|    time_elapsed         | 129          |
|    total_timesteps      | 156160       |
| train/                  |              |
|    approx_kl            | 0.0008088988 |
|    clip_fraction        | 0.000586     |
|    clip_range           | 0.5          |
|    clip_range_vf        | 1e-05        |
|    entropy_loss         | -26.9        |
|    explained_variance   | 0.207        |
|    learning_rate        | 0.1          |
|    loss                 | 150          |
|    n_updates            | 3040         |
|    policy_gradient_loss | 0.00266      |
|    std                  | 1.06e+11     |
|    value_loss           | 317          |
------------------------------------------
-----------

------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 4.83         |
|    ep_rew_mean          | 43.4         |
| time/                   |              |
|    fps                  | 1202         |
|    iterations           | 314          |
|    time_elapsed         | 133          |
|    total_timesteps      | 160768       |
| train/                  |              |
|    approx_kl            | 0.0051985215 |
|    clip_fraction        | 0.0199       |
|    clip_range           | 0.5          |
|    clip_range_vf        | 1e-05        |
|    entropy_loss         | -29.2        |
|    explained_variance   | 0.317        |
|    learning_rate        | 0.1          |
|    loss                 | 68.8         |
|    n_updates            | 3130         |
|    policy_gradient_loss | 0.0112       |
|    std                  | 1.09e+12     |
|    value_loss           | 134          |
------------------------------------------
-----------

---------------------------------------
| rollout/                |           |
|    ep_len_mean          | 4.68      |
|    ep_rew_mean          | 42        |
| time/                   |           |
|    fps                  | 1200      |
|    iterations           | 323       |
|    time_elapsed         | 137       |
|    total_timesteps      | 165376    |
| train/                  |           |
|    approx_kl            | 0.4369908 |
|    clip_fraction        | 0.415     |
|    clip_range           | 0.5       |
|    clip_range_vf        | 1e-05     |
|    entropy_loss         | -32.8     |
|    explained_variance   | 0.176     |
|    learning_rate        | 0.1       |
|    loss                 | 142       |
|    n_updates            | 3220      |
|    policy_gradient_loss | 0.0316    |
|    std                  | 7.61e+13  |
|    value_loss           | 328       |
---------------------------------------
---------------------------------------
| rollout/                |           |


------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 5.03         |
|    ep_rew_mean          | 45.3         |
| time/                   |              |
|    fps                  | 1198         |
|    iterations           | 332          |
|    time_elapsed         | 141          |
|    total_timesteps      | 169984       |
| train/                  |              |
|    approx_kl            | 0.0034145648 |
|    clip_fraction        | 0.00137      |
|    clip_range           | 0.5          |
|    clip_range_vf        | 1e-05        |
|    entropy_loss         | -41.3        |
|    explained_variance   | -0.667       |
|    learning_rate        | 0.1          |
|    loss                 | 114          |
|    n_updates            | 3310         |
|    policy_gradient_loss | 0.000407     |
|    std                  | 1.94e+17     |
|    value_loss           | 243          |
------------------------------------------
-----------

ValueError: Expected parameter loc (Tensor of shape (128, 1)) of distribution Normal(loc: torch.Size([128, 1]), scale: torch.Size([128, 1])) to satisfy the constraint Real(), but found invalid values:
tensor([[nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
    